In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
from scipy.ndimage import gaussian_filter
%matplotlib inline
init_notebook_mode(connected=True)

# Load Data

In [2]:
directory = "C:\\Users\\alexj\\Documents\\Research\\twitter\\parcel_ass\\oc\\"
names = ["event_id", "user_id", "location_id", "lon", "lat", "epoch_time", "day_id", "seconds_since_monday"]
#events = pd.read_csv(directory + "ass_events.csv", header = None, names = names)
data = pd.read_csv(directory + "ass_events_no_filter.csv", header = None, names = names)

In [3]:
data.describe()

event_id       user_id    location_id            lon  \
count  6.559170e+05  6.559170e+05  655917.000000  655917.000000   
mean   6.319007e+06  7.921562e+08  241633.977727    -117.878281   
std    3.652273e+06  1.001908e+09  191189.068282       0.097180   
min    8.000000e+01  2.940000e+02       9.000000    -118.115560   
25%    3.156263e+06  5.413332e+07   61905.000000    -117.922940   
50%    6.301512e+06  2.876739e+08  211459.000000    -117.911910   
75%    9.483557e+06  1.219463e+09  409421.000000    -117.837490   
max    1.272555e+07  4.724669e+09  661044.000000    -117.446930   

                 lat    epoch_time         day_id  seconds_since_monday  
count  655917.000000  6.559170e+05  655917.000000         655917.000000  
mean       33.740011  1.441100e+09     114.426144         324717.879480  
std         0.104993  5.944586e+06      68.802527         174493.396071  
min        33.388260  1.431313e+09       1.000000              2.000000  
25%        33.665890  1.436230e+09      58.000000         162146.000000  
50%        33.778800  1.440782e+09     111.000000         330765.000000  
75%        33.811010  1.446231e+09     174.000000         481287.000000  
max        33.945950  1.452279e+09     244.000000         604798.000000

In [4]:
# round lat, long pairs to fall into discrete bins
data["lat_r"] = data.lat.round(3)
data["lon_r"] = data.lon.round(3)

In [5]:
# calculate counts for heatmap
freqs = data.groupby(['lat_r', 'lon_r']).count().reset_index()[["lat_r", "lon_r", "event_id"]]
freqs.columns = ["lat_r", "lon_r", "freq"]

In [6]:
# heatmap table
p_freqs = freqs.pivot_table(columns="lon_r", index="lat_r", values="freq", fill_value=0)

In [7]:
# remap user id for easier handling
user_dict = {}
index = 0
for ident in data.user_id.unique():
    if ident not in user_dict:
        user_dict[ident] = index
        index += 1

data["new_user_id"] = data.user_id.apply(lambda x: user_dict[x])

# reset day id to start at 0
data["day_id"] = data["day_id"] - data['day_id'].min()

In [8]:
# calculate week and month ids
data["week"] = data.day_id // 7
data['month'] = data.day_id // 30

# determine if you want to plot based on weeks or months
time_used = "week" # "month"

In [9]:
# calculate the number of events within each time period per user
counts2 = data.groupby(["new_user_id", time_used]).count()["event_id"]

In [10]:
# filter based on minimum amount of events per time period (k)
k = 35 #100
view = counts2[counts2 > k].reset_index()

In [11]:
# join together to have a row for each user for a single week joined with the prior and next week
lagged_view = pd.concat([view, view.shift(1), view.shift(2)], axis = 1)
lagged_view.columns = list("next_" + view.columns) + list(view.columns) + list("last_" + view.columns)

In [12]:
# filter rows so that they only contain pairs where there is a sequential week present
right_users = (lagged_view["new_user_id"] == lagged_view["next_new_user_id"]) | (lagged_view["new_user_id"] == lagged_view["last_new_user_id"])
sequential = ((lagged_view["next_"+time_used] - lagged_view[time_used]) == 1) | ((lagged_view[time_used] - lagged_view["last_"+time_used]) == 1)
filtered = lagged_view[right_users & sequential][["new_user_id", time_used, "event_id"]].reset_index(drop=True)
filtered

new_user_id  week  event_id
0            1.0   0.0     204.0
1            1.0   1.0     205.0
2            1.0   2.0     211.0
3            1.0   3.0     250.0
4            1.0   4.0     243.0
5            1.0   5.0     304.0
6            1.0   6.0     146.0
7            1.0   7.0     237.0
8            1.0   8.0     293.0
9            1.0   9.0     297.0
10           1.0  10.0     310.0
11           1.0  11.0     374.0
12           1.0  12.0     392.0
13           1.0  13.0     394.0
14           1.0  14.0     294.0
15           1.0  15.0     365.0
16           1.0  16.0     420.0
17           1.0  17.0     393.0
18           1.0  18.0     364.0
19           1.0  19.0     215.0
20           1.0  21.0     374.0
21           1.0  22.0     117.0
22           1.0  26.0     241.0
23           1.0  27.0     363.0
24           1.0  28.0     269.0
25           1.0  29.0     293.0
26           1.0  30.0     243.0
27           1.0  31.0     235.0
28           3.0  14.0      57.0
29           3.0  15.0      58.0
..           ...   ...       ...
800       8160.0  19.0     110.0
801       8229.0  32.0      71.0
802       8229.0  33.0      40.0
803       8524.0  19.0      93.0
804       8524.0  20.0     114.0
805       8524.0  21.0      78.0
806       9372.0  16.0      49.0
807       9372.0  17.0      37.0
808      10641.0   0.0      55.0
809      10641.0   1.0      64.0
810      10691.0   0.0      68.0
811      10691.0   1.0      76.0
812      10762.0   1.0      45.0
813      10762.0   2.0      53.0
814      10762.0   3.0      47.0
815      10907.0   1.0      45.0
816      10907.0   2.0      41.0
817      10933.0   2.0     101.0
818      10933.0   3.0      43.0
819      10933.0   4.0      38.0
820      13442.0  13.0      78.0
821      13442.0  14.0      44.0
822      14301.0   0.0      67.0
823      14301.0   1.0      82.0
824      17275.0   1.0      50.0
825      17275.0   2.0      84.0
826      17285.0   2.0     160.0
827      17285.0   3.0      99.0
828      25091.0   0.0      62.0
829      25091.0   1.0      43.0

[830 rows x 3 columns]

In [13]:
# gather ids and valid weeks for the users that have survived the filtering
user_time_dict = {-1 : []}
for i, x in filtered.iterrows():
    user_id = x["new_user_id"]
    time = x[time_used]
    if user_id not in user_time_dict:
        user_time_dict[user_id] = []
    user_time_dict[user_id].append(time)

In [14]:
# reduce the original data to be only valid events
reduced_view = pd.merge(left=filtered, right=data, on=["new_user_id", time_used], how="left")

In [15]:
# number of weeks available for analysis
sum([len(v) for k,v in user_time_dict.items()])

830

In [16]:
def get_user(id, time):
    return reduced_view[(reduced_view["new_user_id"] == id) & (reduced_view[time_used] == time)].reset_index(drop=True)

def make_user_scatter_plot(id, time):
    user = get_user(id, time)
    name = "{}-{}{}-{}".format(id, time_used[0], int(time), len(user))
    return go.Scatter(
        x = user.lon,
        y = user.lat,
        mode = 'markers',
        name = name,
        visible = "legendonly"
    )

def plot_figure(user_id):
    heat = go.Heatmap(
        z = gaussian_filter(p_freqs.values, sigma = 0.5).tolist(),
        x = p_freqs.columns,
        y = p_freqs.index,
        colorscale = [
            [0, 'rgb(0, 0, 0)'],        #0
            [1./10000, 'rgb(0, 0, 0)'],
            [1./10000, 'rgb(100, 100, 100)'], #10
            [1./1000, 'rgb(130, 130, 130)'],  #100
            [1./100, 'rgb(170, 170, 170)'],   #1000
            [1./10, 'rgb(220, 220, 220)'],       #10000
            [1., 'rgb(255, 255, 255)'],             #100000

        ],
        colorbar = {
            'tick0': 0,
            'tickmode': 'array',
            'tickvals': [0, 1000, 10000, 100000]
        }
    )

    traces = [heat]
    traces += [make_user_scatter_plot(user_id, time) for time in user_time_dict[user_id]]

    layout = go.Layout(
        legend=dict(x=-.35, y=1)
    )
    fig = go.Figure(data=traces, layout=layout)

    iplot(fig, show_link=False)

In [17]:
#### heatmap only
# -1
#
#### examples
# w: 1358 - concentrated
# w: 907  - very concentrated
# w: 1121 - scattered
# w: 1296 - very concentrated
# w: 13   - clustered w/ outliers
# m: 1409 - identical overlays
# m: 1587 - some clustering
# m: 1725 - extreme clustering
plot_figure(1358)